In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2017 season)
dat <- data[data$period < 24,]
dat <- dat[seq(dim(dat)[1],1),]

In [6]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

Warning message:
"package 'hash' was built under R version 3.6.2"hash-2.2.6.1 provided by Decision Patterns



In [7]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# data$home.number <- home.number
# data$away.number <- away.number

In [9]:
# write.csv(data, 'data.0.csv')

# 2019 Round 1 data

In [4]:
matchup <- data[data$period == 24,]
matchup <- matchup[seq(dim(matchup)[1],1),]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
180 198 2018-03-22 2018   1     24     RI        CA        121       
179 197 2018-03-23 2018   1     24     ES        AD         99       
178 196 2018-03-24 2018   1     24     SK        BL        107       
177 195 2018-03-24 2018   1     24     PA        FR        110       
176 194 2018-03-24 2018   1     24     HW        CW        101       
175 193 2018-03-24 2018   1     24     GC        NM         55       
174 192 2018-03-25 2018   1     24     GW        WB        133       
173 191 2018-03-25 2018   1     24     ME        GE         94       
172 190 2018-03-25 2018   1     24     WC        SY         86       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
180  95        17         ... 1.925                1.990               
179  87        14         ... 1.763                2.110               
178  82        16         ... 1.925                1.877               
177  60        16         ... 1.925                1.862               
176  67        15         ... 1.925                1.909               
175  39         7         ... 1.961                1.961               
174  51        20         ... 1.925                1.925               
173  97        13         ... 1.813                1.925               
172 115        13         ... 1.813                1.925               
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
180 1.990                  1.925                  1.925                
179 2.110                  1.925                  1.925                
178 1.877                  1.925                  1.925                
177 1.862                  1.925                  1.925                
176 1.840                  1.925                  1.925                
175 1.961                  1.925                  1.892                
174 1.925                  1.925                  1.925                
173 1.925                  1.925                  1.925                
172 1.892                  1.925                  1.925                
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
180 2.040                 1.862                         18           1         
179 2.050                 1.769                         14          15         
178 2.040                 1.980                          5           6         
177 1.990                 1.990                         13           7         
176 2.020                 2.020                          8           9         
175 1.990                 1.892                         16           3         
174 1.925                 1.925                          2          12         
173 1.925                 1.925                          4          11         
172 2.050                 1.961                         10          17

# Data

In [5]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [6]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [7]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [8]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [9]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [13]:
#  date ascending order
sflist

[[1]]
Stan model 'Skellam goal and behind difference' does not contain samples.

[[2]]
Stan model 'Skellam goal and behind difference' does not contain samples.

[[3]]
Stan model 'Skellam goal and behind difference' does not contain samples.

[[4]]
Stan model 'Skellam goal and behind difference' does not contain samples.


In [14]:
#  date reverse order
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean    sd    2.5%    25%    50%    75%
delta                      0.67    0.00  0.07    0.52   0.62   0.67   0.71
attackGoals_raw[1,1]       1.80    0.10  2.48   -3.14   0.11   1.84   3.35
attackGoals_raw[1,2]      -4.87    0.09  2.72   -8.90  -7.07  -5.13  -2.92
attackGoals_raw[1,3]      -3.58    0.12  3.16   -8.73  -6.07  -3.78  -1.45
attackGoals_raw[1,4]      -0.17    0.11  2.93   -6.04  -2.12   0.06   1.80
attackGoals_raw[1,5]       0.60    0.10  2.50   -4.33  -1.02   0.53   2.28
attackGoals_raw[1,6]       0.76    0.11  2.78   -4.74  -1.09   0.70   2.73
attackGoals_raw[1,7]      -0.02    0.09  2.29   -4.58  -1.61   0.06   1.52
attackGoals_raw[1,8]       1.06    0.10  2.63   -4.09  -0.70   0.99   2.86
attackGoals_raw[1,9]       1.35    0.07  1.76   -1.99   0.16   1

In [10]:
fit <- sflist2stanfit(sflist)

In [11]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     8.550667e-01 0.0012937417 7.563000e-02    0.70498217
attackGoals_raw[1,1]      2.045149e+00 0.0639279306 2.655077e+00   -2.86745214
attackGoals_raw[1,2]     -1.361123e+00 0.0639193121 3.226650e+00   -7.54220997
attackGoals_raw[1,3]      1.580150e+00 0.0616318292 2.920184e+00   -3.90611230
attackGoals_raw[1,4]     -1.959890e+00 0.0546445797 2.765258e+00   -7.20449206
attackGoals_raw[1,5]      1.216033e+00 0.0567077416 3.141963e+00   -5.14620089
attackGoals_raw[1,6]      1.106832e+00 0.0562316134 2.886234e+00   -4.42976687
attackGoals_raw[1,7]      1.291308e+00 0.0565345883 2.893729e+00   -4.45739282
attackGoals_raw[1,8]      1.794970e-01 0.0467305664 2.694883e+00   -5.04710376
attackGoals_raw[1,9]      1.092478e-01 0.0730395122 3.158855e+00   -5.87889914
attackGoals_raw[1,10]    -3.124245e+00 0.0587628183 3.261357e+00   -8.56229247
attackGoals_raw[1,11]     1.909203e+00 0.06

# Extract parameters

In [12]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [13]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [14]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [15]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [16]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [17]:
# ascending date order
actual.total.diff
correct.vec

[1]  26  12  25  50  34  16  82  -3 -29

[1]  TRUE FALSE  TRUE FALSE  TRUE FALSE  TRUE FALSE FALSE

# Calculate percentage of win, loss and draw

In [18]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [19]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.8896 0.3492 0.9602 0.2962 0.7364 0.4216 0.5144 0.9966 0.6444
      [2,] 0.0438 0.0310 0.0070 0.0282 0.0366 0.0524 0.0206 0.0006 0.0444
      [3,] 0.0666 0.6198 0.0328 0.6756 0.2270 0.5260 0.4650 0.0028 0.3112

In [20]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [21]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [22]:
# Ascending date order
sim.pred.mat

[,1]                [,2]    [,3]    [,4]   [,5]     [,6]   [,7]    [,8]  
 [1,] behind diff         3.2504  1.9458  10.438 3.3176   5.7126 2.3368  0.215 
 [2,] goal diff           6.9724  -1.6856 17.452 -3.1828  1.6704 -1.4704 0.7626
 [3,] total diff          45.0848 -8.1678 115.15 -15.7792 15.735 -6.4856 4.7906
 [4,] home team           RI      ES      SK     PA       HW     GC      GW    
 [5,] away team           CA      AD      BL     FR       CW     NM      WB    
 [6,] actual result       26      12      25     50       34     16      82    
 [7,] prediction correct? TRUE    FALSE   TRUE   FALSE    TRUE   FALSE   TRUE  
 [8,] home win prob       0.8896  0.3492  0.9602 0.2962   0.7364 0.4216  0.5144
 [9,] draw prob           0.0438  0.031   0.007  0.0282   0.0366 0.0524  0.0206
[10,] home loss prob      0.0666  0.6198  0.0328 0.6756   0.227  0.526   0.465 
[11,] simulated sd ests   67.33   45.2    164.44 45.9     33.53  35.78   48.85 
      [,9]     [,10]  
 [1,] 5.1448   0.6222 
 [2,] 45.5454  2.173  
 [3,] 278.4172 13.6602
 [4,] ME       WC     
 [5,] GE       SY     
 [6,] -3       -29    
 [7,] FALSE    FALSE  
 [8,] 0.9966   0.6444 
 [9,] 6e-04    0.0444 
[10,] 0.0028   0.3112 
[11,] 348.86   38.91

In [29]:
write.csv(t(sim.pred.mat),  file = "round1_prediction.csv")